<a href="https://colab.research.google.com/github/schukinam/otus_dl/blob/master/lesson5_TensorFlow2_colab.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Домашнее задание

### Д/з из четырех пунктов:
* Улучшение `fit_generator`
* Сравнение двух ReLU (разные активации)
* Испорченный батч-норм 
* "Сырые" данные. 

### Что нужно сделать
* Следовать инструкциям в каждом из пунктов.
* Результатами вашей работы будет ноутбук с доработанным кодом + архив с директорией с логами `tensorboard` `logs/`, в который вы запишите результаты экспериментов. Подробности в инструкциях ниже.
* Можно и нужно пользоваться кодом из файла `utils`, **но** весь код модифицируйте, пожалуйста, в ноутбуках! Так мне будет проще проверять.

**Загрузка tensorboard в ноутбук**

Можете попробовать использовать его так на свой страх и риск :)

In [1]:
%tensorflow_version 2.x

TensorFlow 2.x selected.


In [2]:
%load_ext tensorboard
%tensorboard --logdir logs

Reusing TensorBoard on port 6006 (pid 146), started 0:09:30 ago. (Use '!kill 146' to kill it.)

<IPython.core.display.Javascript object>

**Импорты**

In [0]:
import tensorflow as tf
import tensorflow.keras as keras
import numpy as np
from typing import Callable

In [4]:
print(tf.__version__)

2.1.0-rc1


### Импорт слоев для д/з

In [0]:
class MNISTSequence(keras.utils.Sequence):
    def __init__(self, X, y, batch_size, preprocess: Callable = None, *args, **kwargs):
        super().__init__()
        self._X = X
        self._y = y
        self._preprocess_fn = preprocess
        self._batch_size = batch_size
        
    def _preprocess(self, X, y):
        if self._preprocess_fn is not None:
            return self._preprocess_fn(X, y)
        return (X / 255.).reshape((-1, 28*28)), y
        
    def __len__(self):
        return int(np.ceil(len(self._X) / float(self._batch_size)))
    
    def __getitem__(self, idx):
        batch_idx = slice(idx*self._batch_size, (idx+1)*self._batch_size, 1)
        x_batch = self._X[batch_idx]  # self._X[idx*self._batch_size:(idx+1)*self._batch_size]
        y_batch = self._y[batch_idx]
        return self._preprocess(x_batch, y_batch)
    
    
class BatchNormFlawed:
    def __init__(self, name):
        self.trainable = True
        self._beta = tf.Variable(0, dtype='float64')
        self._gamma = tf.Variable(1,  dtype='float64')
        self.name = name
        
    def __call__(self, x, writer=None, step=None):
        mu = tf.reduce_mean(x, axis=0)
        sigma = tf.math.reduce_std(x, axis=0)
        normed = (x - mu) / sigma 
        out = normed * self._gamma + self._beta
        
        if writer is not None:
            with writer.as_default():
                tf.summary.histogram(self.name + '_beta', self._beta, step=step)
                tf.summary.histogram(self.name + '_gamma', self._gamma, step=step)
                tf.summary.histogram(self.name + '_normed', normed, step=step)
                tf.summary.histogram(self.name + '_out', out, step=step)
                tf.summary.histogram(self.name + '_sigma', sigma, step=step)
                tf.summary.histogram(self.name + '_mu', mu, step=step)

        return out
    
    def get_trainable(self):
        if self.trainable: 
            return [self._beta, self._gamma]
        else:
            return []

        
from typing import Callable


class Dense:
    def __init__(self, inp_shape, out_shape, activation: Callable, name):
        self.trainable = True
        self._inp_shape = inp_shape
        self._out_shape = out_shape
        self._activation = activation
        
        self._w = tf.Variable(np.random.randn(inp_shape, out_shape))
        self._b = tf.Variable(np.zeros((1, out_shape)))
        
        self.name = name
        
    def __call__(self, x, writer=None, step=None):
        val = x @ self._w + self._b
        a = self._activation(val)
        if writer is not None:
            with writer.as_default():
                tf.summary.histogram(self.name + '_kernel', self._w, step=step)
                tf.summary.histogram(self.name + '_bias', self._b, step=step)
                tf.summary.histogram(self.name + '_activation', a, step=step)
                tf.summary.histogram(self.name + '_z', val, step=step)
        return a
    
    def get_trainable(self):
        if self.trainable: 
            return [self._w, self._b]
        else:
            return []
        
    @property
    def inp_shape(self):
        return self._inp_shape
    
    @property
    def out_shape(self):
        return self._out_shape
    
    @property
    def w(self):
        return self._w
    
    @property
    def b(self):
        return self._b
    
    
class DenseSmart:
    def __init__(self, inp_shape, out_shape, activation: Callable, name):
        self.trainable = True
        self._inp_shape = inp_shape
        self._out_shape = out_shape
        self._activation = activation
        
        if 'sigmoid' in self._activation.__name__:
            self._w = tf.Variable(np.random.rand(inp_shape, out_shape) * np.sqrt(6 / (inp_shape + out_shape)))
        elif 'relu' in self._activation.__name__:
            self._w = tf.Variable(np.random.randn(inp_shape, out_shape) * np.sqrt(2 / (inp_shape)))
        else:
            # Just a Normal
            self._w = tf.Variable(np.random.randn(inp_shape, out_shape))      
        self._b = tf.Variable(np.zeros((1, out_shape)))
        self.name = name
        
    def __call__(self, x, writer=None, step=None):
        val = x @ self._w + self._b
        a = self._activation(val)
        if writer is not None:
            with writer.as_default():
                tf.summary.histogram(self.name + '_kernel', self._w, step=step)
                tf.summary.histogram(self.name + '_bias', self._b, step=step)
                tf.summary.histogram(self.name + '_activation', a, step=step)
                tf.summary.histogram(self.name + '_z', val, step=step)
        return a
    
    def get_trainable(self):
        if self.trainable: 
            return [self._w, self._b]
        else:
            return []
        
    @property
    def inp_shape(self):
        return self._inp_shape
    
    @property
    def out_shape(self):
        return self._out_shape
    
    @property
    def w(self):
        return self._w
    
    @property
    def b(self):
        return self._b
    
    
class Sequential:
    def __init__(self, *args):
        self._layers = args
        self._trainable_variables = [i for s in [l.get_trainable() for l in self._layers] for i in s] 
        
    def _forward(self, x, writer=None, step=None):
        for layer in self._layers:
            x = layer(x, writer, step)
        return x
        
    def fit_generator(self, train_seq, eval_seq, epoch, loss, optimizer, writer=None):
        history = dict(train=list(), val=list())
        
        train_loss_results = list()
        val_loss_results = list()

        train_accuracy_results = list()
        val_accuracy_results = list()
        
        step = 0
        for e in range(epoch):
            p = tf.keras.metrics.Mean()
            epoch_loss_avg = tf.keras.metrics.Mean()
            epoch_loss_avg_val = tf.keras.metrics.Mean()

            epoch_accuracy = tf.keras.metrics.SparseCategoricalAccuracy()
            epoch_accuracy_val = tf.keras.metrics.SparseCategoricalAccuracy()

            for x, y in train_seq:
                with tf.GradientTape() as tape:
                    prediction = self._forward(x, writer, step)
                    loss_value = loss(y, prediction)
                gradients = tape.gradient(loss_value, self._trainable_variables)
                optimizer.apply_gradients(zip(gradients, self._trainable_variables))
                epoch_accuracy.update_state(y, prediction)
                epoch_loss_avg.update_state(loss_value)
                
                with writer.as_default():
                    tf.summary.scalar('train_accuracy', epoch_accuracy.result().numpy(), step=step)
                    tf.summary.scalar('train_loss', epoch_loss_avg.result().numpy(), step=step)

                step += 1
                
            train_accuracy_results.append(epoch_accuracy.result().numpy())
            train_loss_results.append(epoch_loss_avg.result().numpy())


            for x, y in eval_seq:
                prediction = self._forward(x)
                loss_value = loss(y, prediction)
                epoch_loss_avg_val.update_state(loss_value)
                epoch_accuracy_val.update_state(y, prediction)
            
            val_accuracy_results.append(epoch_accuracy_val.result().numpy())
            val_loss_results.append(epoch_loss_avg_val.result().numpy())

            # print(f"Epoch train loss: {epoch_train_loss[-1]:.2f},\nEpoch val loss: {epoch_val_loss[-1]:.2f}\n{'-'*20}")
            print("Epoch {}: Train loss: {:.3f} Train Accuracy: {:.3f}".format(e + 1,
                                                                               train_loss_results[-1],
                                                                               train_accuracy_results[-1]))
            print("Epoch {}: Val loss: {:.3f} Val Accuracy: {:.3f}".format(e + 1,
                                                                           val_loss_results[-1],
                                                                           val_accuracy_results[-1]))
            print('*' * 20)

        return None
            
    def predict_generator(self, seq):
        predictions = list()
        for x in seq:
            predictions.append(self._forward(x).numpy())
        return np.vstack(predictions)
    
    @property
    def trainable_variables(self):
        return self._trainable_variables

### Загрузка данных

> Здесь ничего менять не нужно

In [0]:
(X_tr, y_tr), (X_test, y_test) = keras.datasets.mnist.load_data()

In [0]:
train_seq = MNISTSequence(X_tr, y_tr, 128)
test_seq = MNISTSequence(X_test, y_test, 128)

**Очистка данных**

In [0]:
!rm -rf logs/*

In [0]:
!mkdir -p logs

In [0]:
keras.backend.clear_session()

## 1. Улучшение fit_generator

Улучшите метод `fit_generator` так, чтобы он:
* Записывал значения градиентов для всех переменных при помощи `tf.summary.histogram` 
* Записывал значения ошибки и метрики на валидации с помощью `tf.summary.scalar`

Затем сделайте monkey patch класса sequential обновленным методом (следующая ячейка за методом `fit_generator`).

In [0]:
def fit_generator(self, train_seq, eval_seq, epoch, loss, optimizer, writer=None):
    history = dict(train=list(), val=list())

    train_loss_results = list()
    val_loss_results = list()

    train_accuracy_results = list()
    val_accuracy_results = list()

    step = 0
    for e in range(epoch):
        p = tf.keras.metrics.Mean()
        epoch_loss_avg = tf.keras.metrics.Mean()
        epoch_loss_avg_val = tf.keras.metrics.Mean()

        epoch_accuracy = tf.keras.metrics.SparseCategoricalAccuracy()
        epoch_accuracy_val = tf.keras.metrics.SparseCategoricalAccuracy()
        
        epoch_grad_avg = tf.keras.metrics.Mean()
        epoch_grad_avg_val = tf.keras.metrics.Mean()
        
        # добавленный код
        # вынес формирование списка из цикла
        grad_names = list()
        for layer in self._layers:
            for var_num, _ in enumerate(layer.get_trainable()):
                grad_names.append(f"grad_{layer.name}_{var_num}")
        # конец добавленного кода

        for x, y in train_seq:
            with tf.GradientTape() as tape:
                """
                Обратите внимание! Если записывать гистограмму каждый шаг,
                обучение будет идти очень медленно. Поэтому записываем данные 
                каждый i-й шаг.
                """
                if step % 50 == 0:
                    prediction = self._forward(x, writer, step)
                else:
                    prediction = self._forward(x)
                loss_value = loss(y, prediction)
                     
            ###############################################################
            #                                                             #
            # Добавьте запись градиентов в гистограммы                    #
            #                                                             #
            ###############################################################
        
            gradients = tape.gradient(loss_value, self._trainable_variables)
            
            if step % 50 == 0:
                # добавленный код
                with writer.as_default():
                    for grad_name, gradient in zip(grad_names, gradients):
                        tf.summary.histogram(grad_name, gradient, step=step)
                # конец добавленного кода
            
            optimizer.apply_gradients(zip(gradients, self._trainable_variables))
            epoch_accuracy.update_state(y, prediction)
            epoch_loss_avg.update_state(loss_value)

            if step % 50 == 0:
                with writer.as_default():
                    tf.summary.scalar('train_accuracy', epoch_accuracy.result().numpy(), step=step)
                    tf.summary.scalar('train_loss', epoch_loss_avg.result().numpy(), step=step)

            step += 1

        train_accuracy_results.append(epoch_accuracy.result().numpy())
        train_loss_results.append(epoch_loss_avg.result().numpy())
        
        for x, y in eval_seq:
            prediction = self._forward(x)
            loss_value = loss(y, prediction)
            epoch_loss_avg_val.update_state(loss_value)
            epoch_accuracy_val.update_state(y, prediction)
     
            ###############################################################
            #                                                             #
            # Добавьте сохранение метрики и функции ошибки на валидации   #
            #                                                             #
            ###############################################################

        # добавленный код
        with writer.as_default():
            tf.summary.scalar('val_accuracy', epoch_accuracy_val.result().numpy(), step=e)
            tf.summary.scalar('val_loss', epoch_loss_avg_val.result().numpy(), step=e)
        # конец добавленного кода
            
        val_accuracy_results.append(epoch_accuracy_val.result().numpy())
        val_loss_results.append(epoch_loss_avg_val.result().numpy())

        # print(f"Epoch train loss: {epoch_train_loss[-1]:.2f},\nEpoch val loss: {epoch_val_loss[-1]:.2f}\n{'-'*20}")
        print("Epoch {}: Train loss: {:.3f} Train Accuracy: {:.3f}".format(e + 1,
                                                                           train_loss_results[-1],
                                                                           train_accuracy_results[-1]))
        print("Epoch {}: Val loss: {:.3f} Val Accuracy: {:.3f}".format(e + 1,
                                                                       val_loss_results[-1],
                                                                       val_accuracy_results[-1]))
        print('*' * 20)

    return None

In [0]:
# Monkey patch: обновляем метод
Sequential.fit_generator = fit_generator

## 2. Сравнение двух ReLU (разные активации)

Запустите два эксперимента ниже. Сравните результаты - значения метрик после каждого из них.

Запустите tensorboard, изучите распределения активаций, градиентов и т.д. для `relu` и `smart_dense_relu`. 

Подумайте, почему в одном случае сеть обучается плохо, а в другом - хорошо. Вставьте в ноутбук (или напишите список названий) тех графики из tensorboard, которые, по вашему мнению, это иллюстрируют, и напишите, почему.


Команда для запуска tensorboard в bash:

`$ tensorboard --logdir logs/`

**Ваш комментарий:**

Сеть во втором случае обучается лучше, т.к. веса в первых двух слоях инициализируются по методу Каймина Хе, который заключается в использовании для несимметричных функций активаций инициализацию весов нормальным распределением с нулевым средним и дисперсией $\sqrt{(2/n_{in})}$, где $n_{in}$ - число нейронов во входном слое. 
Использование такой инициализации позволяет успешнее распространяться активациям и градиентам в процессе обучения.
Инициализацию весов можем наблюдать на нулевой итерации графиков (distributions) dense_kernel и dense1_kernel. Разницу в развитии обучений можем наблюдать как на графиках прямого распространения dense_activation, dense1_activation, так и на графиках обратного распространения grad_dense_0, grad_dense1_0, grad_dense2_0 - и активации, и градиенты во втором случае распространяются стабильнее и с меньшей дисперсией.

In [13]:
writer = tf.summary.create_file_writer("logs/relu")

model = Sequential(Dense(784, 100, tf.nn.relu, 'dense'), 
                   Dense(100, 100, tf.nn.relu, 'dense1'), 
                   Dense(100, 10, tf.nn.softmax, 'dense2'))

hist = model.fit_generator(train_seq, test_seq, 10,
                           keras.losses.sparse_categorical_crossentropy, 
                           keras.optimizers.Adam(),
                           writer)

Epoch 1: Train loss: 11.532 Train Accuracy: 0.281
Epoch 1: Val loss: 9.701 Val Accuracy: 0.395
********************
Epoch 2: Train loss: 9.043 Train Accuracy: 0.436
Epoch 2: Val loss: 8.400 Val Accuracy: 0.475
********************
Epoch 3: Train loss: 8.104 Train Accuracy: 0.494
Epoch 3: Val loss: 7.941 Val Accuracy: 0.504
********************
Epoch 4: Train loss: 7.734 Train Accuracy: 0.518
Epoch 4: Val loss: 7.659 Val Accuracy: 0.523
********************
Epoch 5: Train loss: 7.539 Train Accuracy: 0.530
Epoch 5: Val loss: 7.544 Val Accuracy: 0.530
********************
Epoch 6: Train loss: 7.462 Train Accuracy: 0.535
Epoch 6: Val loss: 7.491 Val Accuracy: 0.534
********************
Epoch 7: Train loss: 7.386 Train Accuracy: 0.540
Epoch 7: Val loss: 7.427 Val Accuracy: 0.538
********************
Epoch 8: Train loss: 7.320 Train Accuracy: 0.544
Epoch 8: Val loss: 7.360 Val Accuracy: 0.542
********************
Epoch 9: Train loss: 7.262 Train Accuracy: 0.548
Epoch 9: Val loss: 7.362 Val A

In [14]:
writer = tf.summary.create_file_writer("logs/relu_smart_dense")

model = Sequential(DenseSmart(784, 100, tf.nn.relu, 'dense'), 
                   DenseSmart(100, 100, tf.nn.relu, 'dense1'), 
                   DenseSmart(100, 10, tf.nn.softmax, 'dense2'))

hist = model.fit_generator(train_seq, test_seq, 10,
                           keras.losses.sparse_categorical_crossentropy, 
                           keras.optimizers.Adam(),
                           writer)

Epoch 1: Train loss: 0.346 Train Accuracy: 0.899
Epoch 1: Val loss: 0.185 Val Accuracy: 0.942
********************
Epoch 2: Train loss: 0.130 Train Accuracy: 0.962
Epoch 2: Val loss: 0.138 Val Accuracy: 0.959
********************
Epoch 3: Train loss: 0.088 Train Accuracy: 0.973
Epoch 3: Val loss: 0.124 Val Accuracy: 0.963
********************
Epoch 4: Train loss: 0.064 Train Accuracy: 0.981
Epoch 4: Val loss: 0.113 Val Accuracy: 0.968
********************
Epoch 5: Train loss: 0.049 Train Accuracy: 0.985
Epoch 5: Val loss: 0.117 Val Accuracy: 0.968
********************
Epoch 6: Train loss: 0.039 Train Accuracy: 0.988
Epoch 6: Val loss: 0.110 Val Accuracy: 0.968
********************
Epoch 7: Train loss: 0.032 Train Accuracy: 0.990
Epoch 7: Val loss: 0.132 Val Accuracy: 0.965
********************
Epoch 8: Train loss: 0.028 Train Accuracy: 0.991
Epoch 8: Val loss: 0.125 Val Accuracy: 0.970
********************
Epoch 9: Train loss: 0.024 Train Accuracy: 0.992
Epoch 9: Val loss: 0.143 Val Ac

## 3.a Испорченный батч-норм 

Запустите два эксперимент ниже. 

Почему обучение не идет? В чем ошибка в слое `BatchNorm`? Изучите и исправьте код метода `__call__` (Шаблон находится ниже под блоком с экспериментом.).

Можно пользоваться tensorboard, если он нужен.

## ReLU + Batch Norm

In [15]:
writer = tf.summary.create_file_writer("logs/relu_bn")

model = Sequential(Dense(784, 100, tf.nn.relu, 'dense'), 
                   BatchNormFlawed('batch_norm'), 
                   Dense(100, 100, tf.nn.relu, 'dense1'), 
                   Dense(100, 10, tf.nn.softmax, 'dense2'))

hist = model.fit_generator(train_seq, test_seq, 10,
                           keras.losses.sparse_categorical_crossentropy, 
                           keras.optimizers.Adam(),
                           writer)

Epoch 1: Train loss: nan Train Accuracy: 0.099
Epoch 1: Val loss: nan Val Accuracy: 0.098
********************
Epoch 2: Train loss: nan Train Accuracy: 0.099
Epoch 2: Val loss: nan Val Accuracy: 0.098
********************
Epoch 3: Train loss: nan Train Accuracy: 0.099
Epoch 3: Val loss: nan Val Accuracy: 0.098
********************
Epoch 4: Train loss: nan Train Accuracy: 0.099
Epoch 4: Val loss: nan Val Accuracy: 0.098
********************
Epoch 5: Train loss: nan Train Accuracy: 0.099
Epoch 5: Val loss: nan Val Accuracy: 0.098
********************
Epoch 6: Train loss: nan Train Accuracy: 0.099
Epoch 6: Val loss: nan Val Accuracy: 0.098
********************
Epoch 7: Train loss: nan Train Accuracy: 0.099
Epoch 7: Val loss: nan Val Accuracy: 0.098
********************
Epoch 8: Train loss: nan Train Accuracy: 0.099
Epoch 8: Val loss: nan Val Accuracy: 0.098
********************
Epoch 9: Train loss: nan Train Accuracy: 0.099
Epoch 9: Val loss: nan Val Accuracy: 0.098
********************
E

**Класс, который нужно исправить**

In [0]:
class BatchNormFixed(BatchNormFlawed):
    def __call__(self, x, writer=None, step=None):
        """
        Исправьте блок кода ниже так, чтобы модель обучалась, не появлялись значения loss = NaN        """
        # mu = tf.reduce_mean(x, axis=0)        
        mu = tf.reduce_mean(x, axis=1, keepdims=True)  # исправленная строка
        # sigma = tf.math.reduce_std(x, axis=0)
        sigma = tf.math.reduce_std(x, axis=1, keepdims=True)  # исправленная строка
        normed = (x - mu) / sigma 
        out = normed * self._gamma + self._beta
        """
        Конец блока, который нужно исправить
        """
        
        if writer is not None:
            with writer.as_default():
                tf.summary.histogram(self.name + '_beta', self._beta, step=step)
                tf.summary.histogram(self.name + '_gamma', self._gamma, step=step)
                tf.summary.histogram(self.name + '_normed', normed, step=step)
                tf.summary.histogram(self.name + '_out', out, step=step)
                tf.summary.histogram(self.name + '_sigma', sigma, step=step)
                tf.summary.histogram(self.name + '_mu', mu, step=step)
        return out

## 3.b Исправленный батч-норм 

Запустите эксперимент ниже. 

Обучается ли сеть? Идет ли процесс обучения лучше, чем в эксперименте с ReLU? 

Сравните обучение сетей c ReLU и слоем `Dense` (а не `DenseSmart`!) и ReLU с BatchNorm в tensorboard, как в задании 2.
Напишите ваши выводы.

_Обратите внимание, что слева в интерфейсе tensorboard есть меню, которое позволяет выключать визуализацию ненужных экспериментов._

**Ваш комментарий:**

Да, с BatchNorm сеть обучается лучше, чем без него, даже с плохой инициализацией весов. Слой BatchNorm стоит перед вторым (первым скрытым) слоем, поэтому разницу в работе моделей наблюдаем на графике dense1_activation. Также наблюдаем стабильное распространение градиентов.


In [17]:
writer = tf.summary.create_file_writer("logs/relu_bn_fixed")

model = Sequential(Dense(784, 100, tf.nn.relu, 'dense'), 
                   BatchNormFixed('batch_norm'), 
                   Dense(100, 100, tf.nn.relu, 'dense1'), 
                   Dense(100, 10, tf.nn.softmax, 'dense2'))

hist = model.fit_generator(train_seq, test_seq, 10,
                           keras.losses.sparse_categorical_crossentropy, 
                           keras.optimizers.Adam(),
                           writer)

Epoch 1: Train loss: 9.099 Train Accuracy: 0.412
Epoch 1: Val loss: 4.878 Val Accuracy: 0.650
********************
Epoch 2: Train loss: 1.918 Train Accuracy: 0.724
Epoch 2: Val loss: 0.607 Val Accuracy: 0.809
********************
Epoch 3: Train loss: 0.530 Train Accuracy: 0.832
Epoch 3: Val loss: 0.441 Val Accuracy: 0.865
********************
Epoch 4: Train loss: 0.410 Train Accuracy: 0.872
Epoch 4: Val loss: 0.364 Val Accuracy: 0.889
********************
Epoch 5: Train loss: 0.344 Train Accuracy: 0.894
Epoch 5: Val loss: 0.315 Val Accuracy: 0.906
********************
Epoch 6: Train loss: 0.297 Train Accuracy: 0.909
Epoch 6: Val loss: 0.277 Val Accuracy: 0.916
********************
Epoch 7: Train loss: 0.261 Train Accuracy: 0.921
Epoch 7: Val loss: 0.248 Val Accuracy: 0.924
********************
Epoch 8: Train loss: 0.231 Train Accuracy: 0.930
Epoch 8: Val loss: 0.225 Val Accuracy: 0.930
********************
Epoch 9: Train loss: 0.205 Train Accuracy: 0.939
Epoch 9: Val loss: 0.206 Val Ac

## 4. "Сырые" данные. 

Что будет, если заставить сеть обучаться на сырых данных? 

Напишите такую функцию `preprocess`, которая не делает min-max scaling изображений и оставляет их в изначальном диапазоне. Не убирайте reshape! Конечно, она должна менять форму матрицы входных данных от `(n x 28 x 28)` к `(n x 784)`. 

Затем передайте функцию в MNISTSequence, создайте новую train- и test- последовательности запустите эксперимент, используя их как входные данные. 

Сравните результаты экспериментов c `DenseSmart` + ReLU и обработанными изображениями и `DenseSmart` + ReLU c необработанными изображениями. 

Обучается ли нейросеть? Если нет, то почему? Сделайте выводы, как в задании 2.

**Ваш комментарий:**

Нейросеть не обучается, на графиках градиентов по весам (grad_dense_0, grad_dense1_0, grad_dense2_0) видим, что градиенты нулевые c редкими взрывами. Предположу, что сеть не может пропустить градиенты из-за разных порядков значений весов и входных данных, из-за чего градиентный спуск не может сойтись. Кроме того, в исходном виде данные хранятся в байтах, то есть дискретны, у них низкая точность и через них нельзя пропустить градиент. 

**Шаблон Preprocess**

In [0]:
def preprocess(X, y):
    return X.reshape((-1, 28*28)), y

**Создание генераторов**

In [0]:
train_seq_raw = MNISTSequence(X_tr, y_tr, 128, preprocess=preprocess)
test_seq_raw = MNISTSequence(X_test, y_test, 128, preprocess=preprocess)

**Эксперимент**

In [20]:
writer = tf.summary.create_file_writer("logs/raw")

model = Sequential(DenseSmart(784, 100, tf.nn.relu, 'dense'), 
                   DenseSmart(100, 100, tf.nn.relu, 'dense1'), 
                   DenseSmart(100, 10, tf.nn.softmax, 'dense2'))

hist = model.fit_generator(train_seq_raw, test_seq_raw, 10,
                           keras.losses.sparse_categorical_crossentropy, 
                           keras.optimizers.Adam(),
                           writer
                          )

Epoch 1: Train loss: 14.284 Train Accuracy: 0.114
Epoch 1: Val loss: 14.547 Val Accuracy: 0.097
********************
Epoch 2: Train loss: 14.546 Train Accuracy: 0.098
Epoch 2: Val loss: 14.547 Val Accuracy: 0.097
********************
Epoch 3: Train loss: 14.546 Train Accuracy: 0.098
Epoch 3: Val loss: 14.547 Val Accuracy: 0.097
********************
Epoch 4: Train loss: 14.546 Train Accuracy: 0.098
Epoch 4: Val loss: 14.547 Val Accuracy: 0.097
********************
Epoch 5: Train loss: 14.546 Train Accuracy: 0.098
Epoch 5: Val loss: 14.547 Val Accuracy: 0.097
********************
Epoch 6: Train loss: 14.546 Train Accuracy: 0.098
Epoch 6: Val loss: 14.547 Val Accuracy: 0.097
********************
Epoch 7: Train loss: 14.546 Train Accuracy: 0.098
Epoch 7: Val loss: 14.547 Val Accuracy: 0.097
********************
Epoch 8: Train loss: 14.546 Train Accuracy: 0.098
Epoch 8: Val loss: 14.547 Val Accuracy: 0.097
********************
Epoch 9: Train loss: 14.546 Train Accuracy: 0.098
Epoch 9: Val l